In [ ]:
%matplotlib inline


Custom controls example
-----------------------

Plugging new conrols / actions in Anatomist views



In [ ]:
from __future__ import print_function

from __future__ import absolute_import
import anatomist.direct.api as anatomist
from soma import aims
from soma.aims import colormaphints
import sys
import os
import math
sys.path.insert(0, '.')


# use the right version of Qt and of its python bindings (PyQt4/5/PySide)
from soma.qt_gui.qt_backend import QtCore, QtGui, loadUi

# do we have to run QApplication ?
if QtGui.qApp.startingUp():
    runqt = True
else:
    runqt = False

import sphere

selmesh = None
selanamesh = None


class MyAction(anatomist.cpp.Action):

    def name(self):
        return 'MyAction'

    def resetRadius(self):
        print('reset radius to 1')
        s.setRadius(1.)

    def startMoveRadius(self, x, y, globx, globy):
        print('start move radius', x, y)
        self._initial = (x, y)
        self._radius = s.radius()

    def endMoveRadius(self, x, y, globx, globy):
        print('end move radius', x, y)

    def moveRadius(self, x, y, globx, globy):
        print('move radius', x, y)
        s.setRadius(math.exp(0.01 * (self._initial[1] - y)) * self._radius)

    def takePolygon(self, x, y, globx, globy):
        # print('takePolygon', x, y)

        print('coucou', x, y)

        w = self.view().aWindow()
        obj = w.objectAtCursorPosition(x, y)
        # print('object:', obj)
        if obj is not None:
            print('object:', obj, obj.name())
            poly = w.polygonAtCursorPosition(x, y, obj)
            # print('polygon:', poly)
            mesh = anatomist.cpp.AObjectConverter.aims(obj)
            # print('mesh:', mesh)
            ppoly = mesh.polygon()[poly]
            vert = mesh.vertex()
            # print(ppoly[0], ppoly[1], ppoly[2])
            # print(vert[ppoly[0]], vert[ppoly[1]], vert[ppoly[2]])
            global selmesh, selanamesh
            if selmesh is None:
                selmesh = aims.AimsSurfaceTriangle()
            selmesh.vertex().assign(
                [vert[ppoly[0]], vert[ppoly[1]], vert[ppoly[2]]])
            selmesh.polygon().assign([aims.AimsVector_U32_3(0, 1, 2)])
            if selanamesh is None:
                selanamesh = anatomist.cpp.AObjectConverter.anatomist(selmesh)
                a = anatomist.Anatomist()
                a.execute('SetMaterial', objects=[
                          selanamesh], diffuse=[0, 0, 1., 1.])
                a.execute('AddObject', objects=[selanamesh], windows=[w])
            selanamesh.setChanged()
            selanamesh.notifyObservers()


class MyControl(anatomist.cpp.Control):

    def __init__(self, prio=25):
        anatomist.cpp.Control.__init__(self, prio, 'MyControl')

    def eventAutoSubscription(self, pool):

        key = QtCore.Qt
        NoModifier = key.NoModifier
        ShiftModifier = key.ShiftModifier
        ControlModifier = key.ControlModifier
        AltModifier = key.AltModifier

        self.keyPressEventSubscribe(key.Key_C, NoModifier,
                                    pool.action('MyAction').resetRadius)
        self.mouseLongEventSubscribe(key.LeftButton, NoModifier,
                                     pool.action('MyAction').startMoveRadius,
                                     pool.action('MyAction').moveRadius,
                                     pool.action('MyAction').endMoveRadius,
                                     False)
        self.mousePressButtonEventSubscribe(key.RightButton, NoModifier,
                                            pool.action('MyAction').takePolygon)


a = anatomist.Anatomist()
qapp = QtGui.QApplication.instance()
pix = QtGui.QPixmap('control.xpm')
anatomist.cpp.IconDictionary.instance().addIcon('MyControl', pix)
ad = anatomist.cpp.ActionDictionary.instance()
ad.addAction('MyAction', lambda: MyAction())
cd = anatomist.cpp.ControlDictionary.instance()
cd.addControl('MyControl', lambda: MyControl(), 25)
cm = anatomist.cpp.ControlManager.instance()
cm.addControl('QAGLWidget3D', '', 'MyControl')

s = sphere.ASphere()
a.registerObject(s)
aw = a.createWindow('3D')
a.addObjects([s], [aw])

if 'sphinx_gallery' in sys.modules:
    # display in matplotlib for sphinx_gallery
    import matplotlib
    matplotlib.use('agg', force=True)  # force agg
    aw.imshow(show=True)
    runqt = False
# run Qt
if runqt:
    qapp.exec_()
if runqt or 'sphinx_gallery' in sys.modules:
    del aw, selanamesh, selmesh, s, ad, cd, cm, pix